In [1]:
import pandas as pd
import altair as alt
alt.renderers.enable("html")

RendererRegistry.enable('html')

In [2]:
# Lets ingest our data
df = pd.read_csv(
  'data/abalone.data',
  names=[
    'sex',
    'length',
    'diameter',
    'height',
    'whole_weight',
    'shucked_weight',
    'viscera_weight',
    'shell_weight',
    'rings'
  ]
)

In [3]:
# Lets take a quick look
df.head()

sex  length  diameter  height  whole_weight  shucked_weight  viscera_weight  \
0   M   0.455     0.365   0.095        0.5140          0.2245          0.1010   
1   M   0.350     0.265   0.090        0.2255          0.0995          0.0485   
2   F   0.530     0.420   0.135        0.6770          0.2565          0.1415   
3   M   0.440     0.365   0.125        0.5160          0.2155          0.1140   
4   I   0.330     0.255   0.080        0.2050          0.0895          0.0395   

   shell_weight  rings  
0         0.150     15  
1         0.070      7  
2         0.210      9  
3         0.155     10  
4         0.055      7

In [4]:
# Lets also have a quick describe of our data
df.describe()

length     diameter       height  whole_weight  shucked_weight  \
count  4177.000000  4177.000000  4177.000000   4177.000000     4177.000000   
mean      0.523992     0.407881     0.139516      0.828742        0.359367   
std       0.120093     0.099240     0.041827      0.490389        0.221963   
min       0.075000     0.055000     0.000000      0.002000        0.001000   
25%       0.450000     0.350000     0.115000      0.441500        0.186000   
50%       0.545000     0.425000     0.140000      0.799500        0.336000   
75%       0.615000     0.480000     0.165000      1.153000        0.502000   
max       0.815000     0.650000     1.130000      2.825500        1.488000   

       viscera_weight  shell_weight        rings  
count     4177.000000   4177.000000  4177.000000  
mean         0.180594      0.238831     9.933684  
std          0.109614      0.139203     3.224169  
min          0.000500      0.001500     1.000000  
25%          0.093500      0.130000     8.000000  
50%          0.171000      0.234000     9.000000  
75%          0.253000      0.329000    11.000000  
max          0.760000      1.005000    29.000000

In [5]:
df = df.drop('height', axis=1)

In [6]:
# We first need to convert our sex to a numeric value
def sex_func(sex):
  if sex == 'M':
    return 0
  elif sex == 'F':
    return 1
  return 2

df['sex'] = df['sex'].apply(sex_func)
df.head()

sex  length  diameter  whole_weight  shucked_weight  viscera_weight  \
0    0   0.455     0.365        0.5140          0.2245          0.1010   
1    0   0.350     0.265        0.2255          0.0995          0.0485   
2    1   0.530     0.420        0.6770          0.2565          0.1415   
3    0   0.440     0.365        0.5160          0.2155          0.1140   
4    2   0.330     0.255        0.2050          0.0895          0.0395   

   shell_weight  rings  
0         0.150     15  
1         0.070      7  
2         0.210      9  
3         0.155     10  
4         0.055      7

In [7]:
# Now we need to convert our rings into our 4 classes
# Class 1: 0-7 years (rings)
# Class 2: 8-10 years (rings)
# Class 3: 11-15 years (rings)
# Class 4: > 15 years (rings)

def age_group_func(rings):
  if rings <= 7:
    return 'Class 1: 0-7 Years'
  elif rings <= 10:
    return 'Class 2: 8-10 Years'
  elif rings <= 15:
    return 'Class 3: 11-15 Years'
  else:
    return 'Class 4: > 15 Years'

df['age_group'] = df['rings'].apply(age_group_func)
df.head()

sex  length  diameter  whole_weight  shucked_weight  viscera_weight  \
0    0   0.455     0.365        0.5140          0.2245          0.1010   
1    0   0.350     0.265        0.2255          0.0995          0.0485   
2    1   0.530     0.420        0.6770          0.2565          0.1415   
3    0   0.440     0.365        0.5160          0.2155          0.1140   
4    2   0.330     0.255        0.2050          0.0895          0.0395   

   shell_weight  rings             age_group  
0         0.150     15  Class 3: 11-15 Years  
1         0.070      7    Class 1: 0-7 Years  
2         0.210      9   Class 2: 8-10 Years  
3         0.155     10   Class 2: 8-10 Years  
4         0.055      7    Class 1: 0-7 Years

In [8]:
# Now lets visualise our class distribution
age_group_class_distribution = alt.Chart(df, title="Age Group Class Distribution").mark_bar().encode(
  x=alt.X('age_group:N', title="Age Group", axis=alt.Axis(labelAngle=0)),
  y=alt.Y('count()', title="Count"),
  color=alt.ColorValue('#7BB2D9'),
).properties(
  width=480,
  height=300
)

age_group_class_distribution.save('assets/age_group_class_distribution.png', ppi=100)
age_group_class_distribution

alt.Chart(...)

In [9]:
# Lets also visualise our sex distribution
# Convert our sex column so we can visualise it easier
def sex_undo_func(sex):
  if sex == 0:
    return 'Male'
  elif sex == 1:
    return 'Female'
  return 'Infant'

df_temp = df.copy()
df_temp['sex'] = df_temp['sex'].apply(sex_undo_func)

sex_distribution = alt.Chart(df_temp, title="Sex Distribution").mark_bar().encode(
  x=alt.X('sex:N', title="Sex", axis=alt.Axis(labelAngle=0), sort=None),
  y=alt.Y('count()', title="Count"),
  color=alt.ColorValue('#7BB2D9'),
).properties(
  width=240,
  height=150
)

sex_distribution

alt.Chart(...)

In [10]:
# Now lets visualise our feature distributions
# This gives us an overview of the abalone's physical characteristics
columns = ['length', 'diameter', 'whole_weight', 'shucked_weight', 'viscera_weight', 'shell_weight']
charts = []

for column in columns:
  column_label = column.replace('_', ' ').capitalize()

  charts.append(alt.Chart(df, title=f"{column_label} Distribution").mark_bar().encode(
    x=alt.X(column, title=column_label),
    y=alt.Y(f"count({column}):Q", title=f"{column_label} (count)"),
    color=alt.ColorValue('#7BB2D9'),
  ).properties(
    width=240,
    height=150
  ))

first_row_charts = alt.hconcat(sex_distribution, charts[0], charts[1])
second_row_charts = alt.hconcat(charts[2], charts[3], charts[4])
third_row_charts = alt.hconcat(charts[5])
feature_distributions = alt.vconcat(first_row_charts, second_row_charts, third_row_charts)

feature_distributions.save('assets/feature_distributions.png', ppi=100)
feature_distributions

alt.VConcatChart(...)

In [11]:
# We now really want to see how our features relate to our age groups
# Lets first visulaise our sex and age groups
def sex_undo_func(sex):
  if sex == 0:
    return 'Male'
  elif sex == 1:
    return 'Female'
  return 'Infant'

df_temp = df.copy()
df_temp['sex'] = df_temp['sex'].apply(sex_undo_func)

sex_distribution_by_age = alt.Chart(df_temp, title="Sex Distribution by Age Group").mark_bar().encode(
  x=alt.X('sex:N', title="Sex", axis=alt.Axis(labelAngle=0), sort=None),
  y=alt.Y('count()', title="Sex (count)"),
  color=alt.Color('age_group:N', title="Age Group", scale=alt.Scale(range=['#7BB2D9', '#F5CB5C', '#7FEFBD', '#E85D75'])),
  order=alt.Order('age_group:N')
).properties(
  width=240,
  height=150
)

sex_distribution_by_age

alt.Chart(...)

In [12]:
# Lets use a boxplot to visualise this
columns = ['length', 'diameter', 'whole_weight', 'shucked_weight', 'viscera_weight', 'shell_weight']
charts = []

for column in columns:
  column_label = column.replace('_', ' ').capitalize()

  charts.append(alt.Chart(df, title=f"{column_label} Distribution by Age Group").mark_area(interpolate="step").encode(
    x=alt.X(column, title=column_label).bin(maxbins=100),
    y=alt.Y(f"count({column}):Q", title=f"{column_label} (count)"),
    color=alt.Color("age_group:N").scale(alt.Scale(range=['#7BB2D9', '#F5CB5C', '#7FEFBD', '#E85D75'])),
  ).properties(
    width=240,
    height=150
  ))

first_row_charts = alt.hconcat(sex_distribution_by_age, charts[0], charts[1])
second_row_charts = alt.hconcat(charts[2], charts[3], charts[4])
third_row_charts = alt.hconcat(charts[5])
feature_distributions_by_age_group = alt.vconcat(first_row_charts, second_row_charts, third_row_charts)

feature_distributions_by_age_group.save('assets/feature_distributions_by_age_group.png', ppi=100)
feature_distributions_by_age_group

alt.VConcatChart(...)

In [13]:
# Save the dataframe to a parquet file
df.to_parquet('data/abalone_processed.parquet')